In [33]:
# !pip install -qr requirements.txt

In [153]:
import os
import pandas as pd
import numpy as np
from datetime import datetime
import random
from dateutil.parser import parse
import matplotlib.pyplot as plt
import seaborn as sns

%matplotlib inline
sns.set_style(style = 'whitegrid')
c_palette = ['tab:blue', 'tab:orange']
np.seterr(divide = 'ignore') 
pd.options.mode.chained_assignment = None  # default='warn'

# Loading Data

In [154]:
df_train = pd.read_csv('data/train.csv')
df_test = pd.read_csv('data/test.csv')

In [155]:
df_train.head()

runDate stations  trainCode  trainStationId     scheduledArrival  \
0  2020-01-01      FZR      12138         2657812                  NaN   
1  2020-01-01      FDK      12138         2659393  2020-01-01 22:05:00   
2  2020-01-01      KKP      12138         2658108  2020-01-01 22:23:00   
3  2020-01-01     GJUT      12138         2734206  2020-01-01 22:38:00   
4  2020-01-01      GNA      12138         2742572  2020-01-01 22:54:00   

    scheduledDeparture        actualArrival      actualDeparture  distance  \
0  2020-01-01 21:40:00  2020-01-01 00:00:00  2020-01-01 21:40:00         0   
1  2020-01-01 22:07:00  2020-01-01 22:16:00  2020-01-01 22:18:00        32   
2  2020-01-01 22:25:00  2020-01-01 22:37:00  2020-01-01 22:38:00        45   
3  2020-01-01 22:40:00  2020-01-01 22:56:00  2020-01-01 22:57:00        61   
4  2020-01-01 22:56:00  2020-01-01 23:14:00  2020-01-01 23:15:00        76   

   dayCount  ArrivalDelay  DepartureDelay  
0         0             0               0  
1         0            11              11  
2         0            14              13  
3         0            18              17  
4         0            20              19

In [156]:
df_test.head()

runDate stations  trainId  trainCode  index  trainStationId  \
0  2020-02-20      FZR    11528      12138      1         2657812   
1  2020-02-20      FDK    11528      12138      2         2659393   
2  2020-02-20      KKP    11528      12138      3         2658108   
3  2020-02-20     GJUT    11528      12138      4         2734206   
4  2020-02-20      GNA    11528      12138      5         2742572   

      scheduledArrival   scheduledDeparture  distance  dayCount       day  
0                  NaN  2020-02-20 21:40:00         0         0  Thursday  
1  2020-02-20 22:05:00  2020-02-20 22:07:00        32         0  Thursday  
2  2020-02-20 22:23:00  2020-02-20 22:25:00        45         0  Thursday  
3  2020-02-20 22:38:00  2020-02-20 22:40:00        61         0  Thursday  
4  2020-02-20 22:54:00  2020-02-20 22:56:00        76         0  Thursday

In [157]:
df_train.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 31875 entries, 0 to 31874
Data columns (total 12 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   runDate             31875 non-null  object
 1   stations            31875 non-null  object
 2   trainCode           31875 non-null  int64 
 3   trainStationId      31875 non-null  int64 
 4   scheduledArrival    31184 non-null  object
 5   scheduledDeparture  31097 non-null  object
 6   actualArrival       31875 non-null  object
 7   actualDeparture     31775 non-null  object
 8   distance            31875 non-null  int64 
 9   dayCount            31875 non-null  int64 
 10  ArrivalDelay        31875 non-null  int64 
 11  DepartureDelay      31875 non-null  int64 
dtypes: int64(6), object(6)
memory usage: 2.9+ MB


In [158]:
# pd.options.display.max_info_rows
df_test.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 695 entries, 0 to 694
Data columns (total 11 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   runDate             695 non-null    object
 1   stations            695 non-null    object
 2   trainId             695 non-null    int64 
 3   trainCode           695 non-null    int64 
 4   index               695 non-null    int64 
 5   trainStationId      695 non-null    int64 
 6   scheduledArrival    680 non-null    object
 7   scheduledDeparture  678 non-null    object
 8   distance            695 non-null    int64 
 9   dayCount            695 non-null    int64 
 10  day                 695 non-null    object
dtypes: int64(6), object(5)
memory usage: 59.9+ KB


# EDA

In [7]:
from pandas_profiling import ProfileReport

In [8]:
profile_train = ProfileReport(df_train, title='Profiling Report Train', explorative=True)

In [9]:
# profile.to_file("report.html")
profile_train.to_notebook_iframe()

Summarize dataset:   0%|          | 0/25 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
profile_test = ProfileReport(df_test, title='Profiling Report Test', explorative=True)
profile_test.to_notebook_iframe()

Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Utils

In [159]:
def date_parser(x, date_format):
    try:
        x = datetime.strptime(str(parse(x)), date_format)
        return x, True
    except ValueError:
        return x, False

def dates_to_duration(a, b, duration='day'):
    """
        Utility function to convert dates to duration
    """
    date_format=["%Y-%m-%d %H:%M:%S", "%Y-%m-%dT%H:%M:%S%z", "%Y-%m-%d %H:%M:%S.%f%z"]
    
    for i in date_format:
        p, result = date_parser(a, i)
        if result:
            break
            
    for i in date_format:
        q, result = date_parser(b, i)
        if result:
            break
    
    if duration == 'day':
        return abs((p - q).days)
    if duration == 'hour':
        return abs((p - q)).seconds / 3600
    elif duration == 'minute':
        return abs((p - q)).seconds / 60
    else:
        return abs((p - q)).seconds

In [160]:
def quantitative_summarized(dataframe, x=None, y=None, hue=None, palette='Set1', ax=None, verbose=False, swarm=False):
    """
        Utility function to print summary of a numeric column
    """
    series = dataframe[y]
    print(series.describe())
    print('mode: ', series.mode())
    if verbose:
        print('='*80)
        print(series.value_counts())

    sns.boxplot(x=x, y=y, hue=hue, data=dataframe, palette=palette, ax=ax)

    if swarm:
        sns.swarmplot(x=x, y=y, hue=hue, data=dataframe,
                      palette=palette, ax=ax)

    plt.show()

In [161]:
def categorical_summarized(dataframe, x=None, y=None, hue=None, palette='Set1', verbose=False):
    """
        Utility function to print summary of a categorical column
    """
    if x == None:
        column_interested = y
    else:
        column_interested = x
    series = dataframe[column_interested]
    print(series.describe())
    print('mode: ', series.mode())
    if verbose:
        print('='*80)
        print(series.value_counts())

    sns.countplot(x=x, y=y, hue=hue, data=dataframe, palette=palette)
    plt.show()

In [162]:
# quantitative_summarized(df_cleaned, y = 'quantity', palette=c_palette)
# categorical_summarized(df_cleaned, y = 'status', palette=c_palette)

# Data Preprocessing and Cleaning

In [163]:
# sorting the rows based on trainCode and runDate
df_train = df_train.sort_values(by=['trainCode', 'runDate']).drop_duplicates()
df_test = df_test.sort_values(by=['trainCode', 'runDate']).drop_duplicates()

# # convert trainCode to str since it needs to be categorical
# df['trainCode'] = df['trainCode'].apply(str)

In [164]:
# Calculate travel duration in minutes
df_train['scheduledTravelDuration'] = df_train[['scheduledDeparture', 'scheduledArrival']].apply(lambda x: dates_to_duration(x.scheduledDeparture, x.scheduledArrival, duration='minute') if all(pd.notnull([x.scheduledDeparture, x.scheduledArrival])) else 0, axis=1)
df_test['scheduledTravelDuration'] = df_test[['scheduledDeparture', 'scheduledArrival']].apply(lambda x: dates_to_duration(x.scheduledDeparture, x.scheduledArrival, duration='minute') if all(pd.notnull([x.scheduledDeparture, x.scheduledArrival])) else 0, axis=1)

In [165]:
## Dropping insignificant or unmatching cols 
df_train = df_train.drop(columns=['stations'])
df_test = df_test.drop(columns=['stations', 'day', 'index'])

## Dealing with datetime

In [166]:
df_train['scheduledDeparture'] = pd.to_datetime(df_train['scheduledDeparture'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')
df_train['scheduledArrival'] = pd.to_datetime(df_train['scheduledArrival'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')
df_train['runDate'] = pd.to_datetime(df_train['runDate'], format = '%Y-%m-%d',  errors = 'coerce')
df_train['actualArrival'] = pd.to_datetime(df_train['actualArrival'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')
df_train['actualDeparture'] = pd.to_datetime(df_train['actualDeparture'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')

df_test['scheduledDeparture'] = pd.to_datetime(df_test['scheduledDeparture'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')
df_test['scheduledArrival'] = pd.to_datetime(df_test['scheduledArrival'], format = '%Y-%m-%d %H:%M:%S',  errors = 'coerce')
df_test['runDate'] = pd.to_datetime(df_test['runDate'], format = '%Y-%m-%d',  errors = 'coerce')

In [167]:
for df in [df_train, df_test]:
    # df['scheduledDepartureYear'] = df['scheduledDeparture'].dt.year
    df['scheduledDepartureMonth'] = df['scheduledDeparture'].dt.month
    df['scheduledDepartureWeek'] = df['scheduledDeparture'].dt.week
    df['scheduledDepartureDay'] = df['scheduledDeparture'].dt.day
    df['scheduledDepartureHour'] = df['scheduledDeparture'].dt.hour
    df['scheduledDepartureMinute'] = df['scheduledDeparture'].dt.minute
    df['scheduledDepartureDayofweek'] = df['scheduledDeparture'].dt.dayofweek

/home/rishab/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  after removing the cwd from sys.path.


In [168]:
for df in [df_train, df_test]:
    # df['scheduledArrivalYear'] = df['scheduledArrival'].dt.year
    df['scheduledArrivalMonth'] = df['scheduledArrival'].dt.month
    df['scheduledArrivalWeek'] = df['scheduledArrival'].dt.week
    df['scheduledArrivalDay'] = df['scheduledArrival'].dt.day
    df['scheduledArrivalHour'] = df['scheduledArrival'].dt.hour
    df['scheduledArrivalMinute'] = df['scheduledArrival'].dt.minute
    df['scheduledArrivalDayofweek'] = df['scheduledArrival'].dt.dayofweek

/home/rishab/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  after removing the cwd from sys.path.


In [169]:
for df in [df_train, df_test]:
    # df['runDateYear'] = df['runDate'].dt.year
    df['runDateMonth'] = df['runDate'].dt.month
    df['runDateWeek'] = df['runDate'].dt.week
    df['runDateDay'] = df['runDate'].dt.day

/home/rishab/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  after removing the cwd from sys.path.


In [170]:
## Dropping datetime cols
df_train = df_train.drop(columns=df_train.select_dtypes(include=['datetime64']).columns)
df_test = df_test.drop(columns=df_test.select_dtypes(include=['datetime64']).columns)

In [171]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 31875 entries, 0 to 31874
Data columns (total 22 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   trainCode                    31875 non-null  int64  
 1   trainStationId               31875 non-null  int64  
 2   distance                     31875 non-null  int64  
 3   dayCount                     31875 non-null  int64  
 4   ArrivalDelay                 31875 non-null  int64  
 5   DepartureDelay               31875 non-null  int64  
 6   scheduledTravelDuration      31875 non-null  float64
 7   scheduledDepartureMonth      31097 non-null  float64
 8   scheduledDepartureWeek       31097 non-null  float64
 9   scheduledDepartureDay        31097 non-null  float64
 10  scheduledDepartureHour       31097 non-null  float64
 11  scheduledDepartureMinute     31097 non-null  float64
 12  scheduledDepartureDayofweek  31097 non-null  float64
 13  scheduledArrival

## Handling Missing Values & Categorical Cols

In [172]:
df_train = df_train.replace([np.inf, -np.inf], np.nan)
df_train[df_train.select_dtypes(include=['int64']).columns] = df_train[df_train.select_dtypes(include=['int64']).columns].fillna(0)
df_train[df_train.select_dtypes(include=['float64']).columns] = df_train[df_train.select_dtypes(include=['float64']).columns].fillna(0.)
# df_train[df_train.select_dtypes(include=['object']).columns].fillna('unattributed', inplace=True)
# df_train = pd.get_dummies(df_train, columns=df_train.select_dtypes(include=['object']).columns)

df_test = df_test.replace([np.inf, -np.inf], np.nan)
df_test[df_test.select_dtypes(include=['int64']).columns] = df_test[df_test.select_dtypes(include=['int64']).columns].fillna(0)
df_test[df_test.select_dtypes(include=['float64']).columns] = df_test[df_test.select_dtypes(include=['float64']).columns].fillna(0.)
# df_test[df_test.select_dtypes(include=['object']).columns].fillna('unattributed', inplace=True)
# df_test = pd.get_dummies(df_test, columns=df_test.select_dtypes(include=['object']).columns)

In [173]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 31875 entries, 0 to 31874
Data columns (total 22 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   trainCode                    31875 non-null  int64  
 1   trainStationId               31875 non-null  int64  
 2   distance                     31875 non-null  int64  
 3   dayCount                     31875 non-null  int64  
 4   ArrivalDelay                 31875 non-null  int64  
 5   DepartureDelay               31875 non-null  int64  
 6   scheduledTravelDuration      31875 non-null  float64
 7   scheduledDepartureMonth      31875 non-null  float64
 8   scheduledDepartureWeek       31875 non-null  float64
 9   scheduledDepartureDay        31875 non-null  float64
 10  scheduledDepartureHour       31875 non-null  float64
 11  scheduledDepartureMinute     31875 non-null  float64
 12  scheduledDepartureDayofweek  31875 non-null  float64
 13  scheduledArrival

## Data Preparation

In [174]:
from sklearn.preprocessing import MinMaxScaler, RobustScaler
from sklearn.model_selection import train_test_split

In [175]:
robust_scaler = RobustScaler() 
minmax_scaler = MinMaxScaler() 

In [176]:
df_train['distance'] = minmax_scaler.fit_transform(np.array(df_train['distance']).reshape(-1, 1))
df_test['distance'] = minmax_scaler.fit_transform(np.array(df_test['distance']).reshape(-1, 1))

df_train['scheduledTravelDuration'] = minmax_scaler.fit_transform(np.array(df_train['scheduledTravelDuration']).reshape(-1, 1))
df_test['scheduledTravelDuration'] = minmax_scaler.fit_transform(np.array(df_test['scheduledTravelDuration']).reshape(-1, 1))

In [177]:
# sort a dataframe based on column names 
df_train = df_train.sort_index(axis = 1) 
df_test = df_test.sort_index(axis = 1) 

In [178]:
X = df_train.drop(columns=['ArrivalDelay', 'DepartureDelay'])
y = df_train[['ArrivalDelay', 'DepartureDelay']]

In [179]:
train_columns = list(X.columns)

In [180]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size = 0.10, random_state = 123, shuffle=True)

# Delay Estimation

In [181]:
# self-defined eval metric
# f(y_true: array, y_pred: array) -> name: string, eval_result: float, is_higher_better: bool
# Root Mean Squared Logarithmic Error (RMSLE)
def rmsle(y_true, y_pred):
    return 'RMSLE', np.sqrt(np.mean(np.power(np.log1p(y_pred) - np.log1p(y_true), 2))), False

# f(y_true: array, y_pred: array) -> name: string, eval_result: float, is_higher_better: bool
# Relative Absolute Error (RAE)
def rae(y_true, y_pred):
    return 'RAE', np.sum(np.abs(y_pred - y_true)) / np.sum(np.abs(np.mean(y_true) - y_true)), False

## RandomForestRegressor

In [182]:
import os
import joblib
import matplotlib.pyplot as plt

# Feature Importance by Tree-based estimators
from sklearn.ensemble import RandomForestRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import cross_val_score, RepeatedKFold
from sklearn.model_selection import RepeatedKFold

## Hyperparameter Tuning

In [183]:
def hyperparameterOptimizationRFR(X, y):
    # RandomizedSearchCV
    # Number of trees in random forest
    n_estimators = [int(x) for x in np.linspace(start = 100, stop = 1000, num = 100)]
    # Number of features to consider at every split
    max_features = ['auto', 'sqrt']
    # Maximum number of levels in tree
    max_depth = [int(x) for x in np.linspace(1, 10, num = 2)]
    max_depth.append(None)
    # Minimum number of samples required to split a node
    min_samples_split = [2,4,7]
    # Minimum number of samples required at each leaf node
    min_samples_leaf = [1, 2, 4]
    # Method of selecting samples for training each tree
    bootstrap = [True, False]
    # Create the random grid
    random_grid = {'n_estimators': n_estimators,
                   'max_features': max_features,
                   'max_depth': max_depth,
                   'min_samples_split': min_samples_split,
                   'min_samples_leaf': min_samples_leaf,
                   'bootstrap': bootstrap}

    rf = RandomForestRegressor()
    # Random search of parameters, using 3 fold cross validation,
    # search across 100 different combinations, and use all available cores
    rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 25, cv = 3, verbose=2, random_state=42, n_jobs = -1)
    # Fit the random search model
    rf_random.fit(X,  y)
    return rf_random

In [184]:
# Getting the best hyper parameters
hp = hyperparameterOptimizationRFR(X_train,  y_train)
hp = hp.best_params_
print('Best hyperparameters:', hp)

Fitting 3 folds for each of 25 candidates, totalling 75 fits
Best hyperparameters: {'n_estimators': 336, 'min_samples_split': 7, 'min_samples_leaf': 4, 'max_features': 'auto', 'max_depth': None, 'bootstrap': True}


## Training

In [185]:
# Parameter values
regressor = RandomForestRegressor(n_estimators = hp['n_estimators'],min_samples_split = hp['min_samples_split'],
                                       min_samples_leaf = hp['min_samples_leaf'], max_features = hp['max_features'],
                                       max_depth = hp['max_depth'], bootstrap = hp['bootstrap'], n_jobs=-1)
wrapper = MultiOutputRegressor(regressor, n_jobs=-1)

# Fitting RFR to the Training set
regressor.fit(X_train, y_train)

RandomForestRegressor(min_samples_leaf=4, min_samples_split=7, n_estimators=336,
                      n_jobs=-1)

In [187]:
# Top 15 most weighted features
pd.Series(regressor.feature_importances_, index = X.columns).nlargest(15).plot(kind = 'barh',
                                                                                      figsize = (10, 10),
                                                                                      title = 'Feature importance from RandomForest').invert_yaxis()

In [188]:
wrapper = MultiOutputRegressor(regressor)
# Fitting MultiOutputRegressor to the Training set
wrapper.fit(X_train, y_train)

MultiOutputRegressor(estimator=RandomForestRegressor(min_samples_leaf=4,
                                                     min_samples_split=7,
                                                     n_estimators=336,
                                                     n_jobs=-1))

### Prediction and Evaluation

In [189]:
# define the evaluation procedure
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
# evaluate the model and collect the scores
n_scores = cross_val_score(wrapper, X, y, scoring='neg_mean_absolute_error', cv=cv, n_jobs=-1)
# force the scores to be positive
n_scores = np.absolute(n_scores)
# summarize performance
print('MAE: %.3f (%.3f)' % (np.mean(n_scores), np.std(n_scores)))

/home/rishab/anaconda3/lib/python3.7/site-packages/joblib/externals/loky/process_executor.py:691: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  "timeout or by a memory leak.", UserWarning


MAE: 13.219 (0.379)


In [190]:
print('Starting predicting...')
# predict
y_pred = wrapper.predict(X_val)
# eval
print('The rmse of prediction is:', mean_squared_error(y_val, y_pred) ** 0.5)
print('\nThe rmsle of prediction is:\n', rmsle(y_val, y_pred)[1])
print('\nThe rae of prediction is:\n', rae(y_val, y_pred)[1])

Starting predicting...
The rmse of prediction is: 23.450129909103822

The rmsle of prediction is:
 ArrivalDelay           inf
DepartureDelay    0.924652
dtype: float64

The rae of prediction is:
 ArrivalDelay      0.335130
DepartureDelay    0.329946
dtype: float64


/home/rishab/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: RuntimeWarning: invalid value encountered in log1p
  """


## LightGBM

In [191]:
# coding: utf-8
import numpy as np
import pandas as pd
import lightgbm as lgb

from sklearn.metrics import mean_squared_error
from sklearn.model_selection import GridSearchCV
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform

In [192]:
print('Starting training...')
estimator = lgb.LGBMRegressor(random_state=101)

param_grid ={
             'num_leaves': sp_randint(6, 50), 
             'min_child_samples': sp_randint(100, 500), 
             'min_child_weight': [1e-5, 1e-3, 1e-2, 1e-1, 1, 1e1, 1e2, 1e3, 1e4],
             'subsample': sp_uniform(loc=0.2, scale=0.8), 
             'colsample_bytree': sp_uniform(loc=0.4, scale=0.6),
             'reg_alpha': [0, 1e-1, 1, 2, 5, 7, 10, 50, 100],
             'reg_lambda': [0, 1e-1, 1, 5, 10, 20, 50, 100]
            }
    
# Random search of parameters, using 3 fold cross validation,
gbm = RandomizedSearchCV(
                estimator=estimator, param_distributions=param_grid, 
                n_iter=25,
                cv=3,
                random_state=314,
                refit=True,
                verbose=True,
                n_jobs = -1)

# Fit the random search model
model = MultiOutputRegressor(gbm, n_jobs=-1)
result = model.fit(X_train, y_train)

print('Starting completed!')

Starting training...
Starting completed!


### Prediction and Evaluation

In [193]:
# define the evaluation procedure
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
# evaluate the model and collect the scores
n_scores = cross_val_score(model, X, y, scoring='neg_mean_absolute_error', cv=cv, n_jobs=-1)
# force the scores to be positive
n_scores = np.absolute(n_scores)
# summarize performance
print('MAE: %.3f (%.3f)' % (np.mean(n_scores), np.std(n_scores)))

MAE: 35.974 (0.742)


In [194]:
print('Starting predicting...')
# predict
y_pred = model.predict(X_val)
# eval
print('The rmse of prediction is:', mean_squared_error(y_val, y_pred) ** 0.5)
print('\nThe rmsle of prediction is:\n', rmsle(y_val, y_pred)[1])
print('\nThe rae of prediction is:\n', rae(y_val, y_pred)[1])

Starting predicting...
The rmse of prediction is: 36.65187242033325

The rmsle of prediction is:
 ArrivalDelay           inf
DepartureDelay    1.215408
dtype: float64

The rae of prediction is:
 ArrivalDelay      0.565488
DepartureDelay    0.560845
dtype: float64


/home/rishab/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: RuntimeWarning: invalid value encountered in log1p
  """
